In [1]:
import os, glob, re, io, random, gensim, smart_open, logging
import numpy as np

from PyPDF2 import PdfReader
from pdfminer.high_level import extract_text as fallback_text_extraction
from gensim.models.doc2vec import Doc2Vec, TaggedDocument
from gensim.test.utils import get_tmpfile
from nltk.tokenize import word_tokenize


In [2]:
pdfReaders = []
pdfFiles = []
docLabels = []

# taggedData = []
# wordSets = []

logging.basicConfig(format='%(asctime)s : %(levelname)s : %(message)s', level=logging.INFO)
rootDir = "/Users/tillman/t-root/dev/projects/2022/pdf-correlator/gitignored"
txtExtractDir = "/Users/tillman/t-root/dev/projects/2022/pdf-correlator/gitignored/txt-extractions/"
zoteroDir = '/Users/tillman/t-root/zotero/storage'

stoplist = set('for a of the and to in'.split(' '))

In [3]:
# read files
def read_files():
    os.chdir(rootDir)
    for file in glob.glob("**/*.pdf"):
        pdfFiles.append(file)
        pdfReaders.append(PdfReader(file))
    print("pdf files read")
            
read_files()

pdf files read


In [4]:
def extract_to_txt():
    os.chdir(txtExtractDir)
    pat0 = ('(?<!Dr)(?<!Esq)\. +(?=[A-Z])')
    pat1 = ('\.+(?=[A-Z])')
    pat2 = ('\.+(?=[0-9])')
    pat3 = ('\. +(?=[0-9])')
    pat4 = ('(?=[for a of the and to in])')
    
    patterns = [pat0, pat1, pat2, pat3, pat4]
    counter = 0
    for i in pdfReaders:
        counter += 1
        print(counter)
        with open(str([i.metadata.title]) + ".txt", 'w', encoding="utf-8") as file:
            
            # add doc title to array for reference / tagging
            docLabels.append(i.metadata.title)
            print(i.metadata.title)
            try:
                for j in range(len(i.pages)):
                    # format txt file so that each line is one sentence (doc2vec requirement)
                    text = i.getPage(j).extract_text()
                    text = re.sub(patterns[0], '.\n', text)
                    text = re.sub(patterns[1], '.\n', text)
                    text = re.sub(patterns[2], '.\n', text)
                    text = re.sub(patterns[3], '.\n', text)
                    text = re.sub(patterns[4], '', text)
                    file.write(text)   
                    
            except Exception as exc:
                    print(">>>>> exception")
                    # format txt file so that each line is one sentence (doc2vec requirement)
                    text = fallback_text_extraction(rootDir + "/" + pdfFiles[counter])
                    text = re.sub(patterns[0], '.\n', text)
                    text = re.sub(patterns[1], '.\n', text)
                    text = re.sub(patterns[2], '.\n', text)
                    text = re.sub(patterns[3], '.\n', text)
                    text = re.sub(patterns[4], '', text)
                    file.write(text)   


extract_to_txt()




1
Arts and design as translational mechanisms for academic entrepreneurship_ The metaLAB at Harvard case study
2
pone.0099019 1..8
3
None
4
User attention and behaviour in virtual reality art encounter
5
Microsoft Word - CHI2018_LucidDreaming_v5.docx
6
Microsoft Word - 48710116.DOC
7
frvir-2022-779148 1..5
8
Making Art Therapy Virtual: Integrating Virtual Reality Into Art Therapy With Adolescents
9
None
10
Making Art Therapy Virtual: Integrating Virtual Reality Into Art Therapy With Adolescents
11
Microsoft Word - LeavingVR_Finals.docx
12
ShareVR: Enabling Co-Located Experiences for Virtual Reality between HMD and Non-HMD Users
13
None
>>>>> exception
14
Kafka:Reimagined – A Non-Linear Reinterpretation in VR
15
The effects of visual context and individual differences on perception and evaluation of modern art and graffiti art
16
IAFOR Journal of Cultural Studies – Volume 6 – Issue 1 
17
g5grap.lo
18
User attention and behaviour in virtual reality art encounter
19
ShareVR: Enabling Co-L

In [32]:
class CorpusGen(object):
    def __init__(self, dirname):
        self.dirname = dirname
 
    def __iter__(self, tokens_only=False):
        for fname in os.listdir(self.dirname):
            with smart_open.open(fname, encoding="iso-8859-1") as f:
                for i, line in enumerate(f):
                    tokens = gensim.utils.simple_preprocess(line, min_len=2, max_len=15, deacc=True)
                    if tokens_only:
                        yield tokens
                    else:
                        yield gensim.models.doc2vec.TaggedDocument(tokens, [i])

trainCorpus = list(CorpusGen('/Users/tillman/t-root/dev/projects/2022/pdf-correlator/gitignored/txt-extractions'))


print(list(trainCorpus))

[TaggedDocument(words=['bud', 'dsdb'], tags=[0]), TaggedDocument(words=['xml', 'version', 'encoding', 'utf'], tags=[0]), TaggedDocument(words=['html'], tags=[1]), TaggedDocument(words=['head'], tags=[2]), TaggedDocument(words=['meta', 'charset', 'utf'], tags=[3]), TaggedDocument(words=['head'], tags=[4]), TaggedDocument(words=['body'], tags=[5]), TaggedDocument(words=['ul', 'id', 'a_l', 'fopj'], tags=[6]), TaggedDocument(words=['li', 'id', 'wd'], tags=[7]), TaggedDocument(words=['contents', 'lists', 'available', 'atsciencedirect'], tags=[8]), TaggedDocument(words=['li'], tags=[9]), TaggedDocument(words=['li', 'id', 'wb'], tags=[10]), TaggedDocument(words=['journal', 'of', 'business', 'research'], tags=[11]), TaggedDocument(words=['li'], tags=[12]), TaggedDocument(words=['li', 'id'], tags=[13]), TaggedDocument(words=['journal', 'homepage', 'www', 'elsevier', 'com', 'locate', 'jbusres'], tags=[14]), TaggedDocument(words=['li'], tags=[15]), TaggedDocument(words=['li', 'id', 'ht'], tags=[1

In [33]:
# establish a model and build the vocab

model = gensim.models.doc2vec.Doc2Vec(vector_size=50, min_count=1, epochs=40)
model.build_vocab(trainCorpus)


2022-09-27 12:26:34,821 : INFO : Doc2Vec lifecycle event {'params': 'Doc2Vec<dm/m,d50,n5,w5,s0.001,t3>', 'datetime': '2022-09-27T12:26:34.821153', 'gensim': '4.2.0', 'python': '3.10.6 | packaged by conda-forge | (main, Aug 22 2022, 20:41:22) [Clang 13.0.1 ]', 'platform': 'macOS-12.0.1-arm64-arm-64bit', 'event': 'created'}
2022-09-27 12:26:34,828 : INFO : collecting all words and their counts
2022-09-27 12:26:34,829 : INFO : PROGRESS: at example #0, processed 0 words (0 words/s), 0 word types, 0 tags
2022-09-27 12:26:34,843 : INFO : PROGRESS: at example #10000, processed 42654 words (3319366 words/s), 8153 word types, 0 tags
2022-09-27 12:26:34,855 : INFO : PROGRESS: at example #20000, processed 87006 words (3880753 words/s), 12997 word types, 0 tags
2022-09-27 12:26:34,866 : INFO : PROGRESS: at example #30000, processed 118331 words (3272636 words/s), 16326 word types, 0 tags
2022-09-27 12:26:34,873 : INFO : collected 18838 word types and 37122 unique tags from a corpus of 37123 exampl

In [34]:
# check word occurence
print(f"Word 'the' appeared {model.wv.get_vecattr('the', 'count')} times in the training corpus.")

Word 'the' appeared 5696 times in the training corpus.


In [35]:
model.train(trainCorpus, total_examples=model.corpus_count, epochs=model.epochs)

2022-09-27 12:26:44,845 : INFO : Doc2Vec lifecycle event {'msg': 'training model with 3 workers on 18838 vocabulary and 50 features, using sg=0 hs=0 sample=0.001 negative=5 window=5 shrink_windows=True', 'datetime': '2022-09-27T12:26:44.845831', 'gensim': '4.2.0', 'python': '3.10.6 | packaged by conda-forge | (main, Aug 22 2022, 20:41:22) [Clang 13.0.1 ]', 'platform': 'macOS-12.0.1-arm64-arm-64bit', 'event': 'train'}
2022-09-27 12:26:45,398 : INFO : EPOCH 0: training on 144173 raw words (132112 effective words) took 0.5s, 247033 effective words/s
2022-09-27 12:26:45,908 : INFO : EPOCH 1: training on 144173 raw words (132054 effective words) took 0.5s, 262679 effective words/s
2022-09-27 12:26:46,434 : INFO : EPOCH 2: training on 144173 raw words (131994 effective words) took 0.5s, 255089 effective words/s
2022-09-27 12:26:47,004 : INFO : EPOCH 3: training on 144173 raw words (131992 effective words) took 0.6s, 234701 effective words/s
2022-09-27 12:26:47,522 : INFO : EPOCH 4: training 

In [36]:
# infer a vector from corupus (I dont actually know what this means or does! :D )
vector = model.infer_vector(['only', 'you', 'can', 'prevent', 'forest', 'fires'])
print("infering a vector:")
print(vector)

infering a vector:
[ 0.02854667  0.08201747 -0.06977796  0.06210873 -0.17147933 -0.16357218
  0.00490393  0.4040195  -0.16186854 -0.07179262 -0.02978029 -0.00889829
  0.15205838  0.07703431  0.05068703  0.03470878  0.26976582  0.18049286
 -0.19366026 -0.30539876  0.06896118 -0.16064736  0.0971634  -0.18964864
  0.08859878  0.0463131  -0.02349368 -0.00424384 -0.12951425  0.02845228
  0.10165736 -0.08577621  0.07486299 -0.17416699 -0.21999516  0.10245397
 -0.0979223  -0.1615363  -0.01153289 -0.01628953  0.07254513 -0.02792765
 -0.11273327 -0.00690204  0.10164902  0.08673603 -0.01782459 -0.11584652
 -0.08261226  0.1196695 ]


In [37]:
print(list(trainCorpus))

[TaggedDocument(words=['bud', 'dsdb'], tags=[0]), TaggedDocument(words=['xml', 'version', 'encoding', 'utf'], tags=[0]), TaggedDocument(words=['html'], tags=[1]), TaggedDocument(words=['head'], tags=[2]), TaggedDocument(words=['meta', 'charset', 'utf'], tags=[3]), TaggedDocument(words=['head'], tags=[4]), TaggedDocument(words=['body'], tags=[5]), TaggedDocument(words=['ul', 'id', 'a_l', 'fopj'], tags=[6]), TaggedDocument(words=['li', 'id', 'wd'], tags=[7]), TaggedDocument(words=['contents', 'lists', 'available', 'atsciencedirect'], tags=[8]), TaggedDocument(words=['li'], tags=[9]), TaggedDocument(words=['li', 'id', 'wb'], tags=[10]), TaggedDocument(words=['journal', 'of', 'business', 'research'], tags=[11]), TaggedDocument(words=['li'], tags=[12]), TaggedDocument(words=['li', 'id'], tags=[13]), TaggedDocument(words=['journal', 'homepage', 'www', 'elsevier', 'com', 'locate', 'jbusres'], tags=[14]), TaggedDocument(words=['li'], tags=[15]), TaggedDocument(words=['li', 'id', 'ht'], tags=[1

In [41]:
# assessing the model
ranks = []
secondRanks = []
for doc_id in range(len(trainCorpus)):
        inferredVector = model.infer_vector(trainCorpus[doc_id].words)
        sims = model.dv.most_similar([inferredVector], topn=len(model.dv))
        rank = [docid for docid, sim in sims].index(doc_id)
        ranks.append(rank)
        
        
        secondRanks.append(sims[1])

ValueError: 37122 is not in list

In [43]:
# for doc_id in range(len(trainCorpus)):
#     print(doc_id)

print(len(model.dv))

37122


In [ ]:
import collections

counter = collections.Counter(ranks)
print(counter)


In [ ]:
print('Document ({}): «{}»\n'.format(doc_id, ' '.join(trainCorpus[doc_id].words)))
print(u'SIMILAR/DISSIMILAR DOCS PER MODEL %s:\n' % model)
for label, index in [('MOST', 0), ('SECOND-MOST', 1), ('MEDIAN', len(sims)//2), ('LEAST', len(sims) - 1)]:
    print(u'%s %s: «%s»\n' % (label, sims[index], ' '.join(trainCorpus[sims[index][0]].words)))